### Skill to vector - 2. Data cleaning

In [1]:
## Import modules
import pandas as pd
import numpy as np
import scipy.sparse as sps
import matplotlib.pyplot as plt
import progressbar as pp
import re
from tqdm import tqdm
import nltk
from nltk.corpus imeport stopwords
from nltk.tokenize import word_tokenize
import random
import pickle

In [2]:
## load data - 1 million in total
job_description_df = pd.read_csv("/mnt/c/Users/ruihao/Documents/Data/job_description_all_1m.csv")

In [4]:
## pre-analysis
## extract english job descriptions - 400k in total

# filter out short job description (<100 words)
job_description_en_df = pd.DataFrame(job_description_df[job_description_df.language_id==1]["job_description"].dropna())
job_description_en_df = job_description_en_df[job_description_en_df["job_description"].apply(lambda x: len(x.split())>100)]

In [20]:
## An example
n = random.randint(0, len(job_description_en_df))
example = job_description_en_df.iloc[n].values[0]
print(example)

![](https://l.gpcdn.pl/3/30/306/306063/_res/top.jpg)

.Net Developer (Full Stack)

Location: Gdańsk  

The challenges waiting for you:

  

For our international customer – specializing in producing computer hardware -
we are currently looking for an experienced .NET Developer.

The project concerns the development of web application for hardware usage
tracking. On each setup there is an application that collects and sends data
to serwers. In this web application users can display information that they
are interested in. Another part of project will be development of a system
responsible for tracking physical location of hardware



Responsibilities:

  * Developing of web based frontend solutions using JS, Angular
  * Developing with MSSQL
  * Implementing unit testing as natural part of the development process (xUnit)

Required skills:

  

  * At least 1-2 years of commercial experience
  * C# .NET 4.6+, MVC
  * JS, Angular
  * Bootstrap, MS SQL, Entity Framework
  * Experience with

In [19]:
## Pre-pocessing for the example

def paragraph_segment(text):
    text = re.sub(r"[\(\>]http.+?(\n.+?)*[\)\>]", " ", text, re.MULTILINE) ## remove url
    text = re.split("\n[\s]*\n", text) ## segment with double newlines
    text = [re.sub(r"[^\w\&]", " ", x) for x in text] ## remove special characters
    
    text = [re.sub(r"[\s]+", " ", x.strip()) for x in text] ## remove spaces
    text = list(filter(lambda x: len(x.split())>2, text)) ## remove short sentences
    return text

paragraph_segment(example)

['Send me Jobs like this',
 'Assist clients in their recruitment and hiring through Online job portal',
 'Provide Product & Recruitment Training to Clients',
 'Engage with key clients and building long term client relationships to generate repeat business and referrals',
 '_Salary _ INR 2 50 000 4 50 000 P A',
 '_Industry _ Internet Ecommerce',
 '_Functional Area _ Sales Retail Business Development',
 '_Role Category _ Channel Sales',
 '_Role _ Client Relationship Manager',
 '_Employment Type _ Permanent Job Full Time',
 'Client Relationship Manager client relationship management jobs Find all jobs matching Client Relationship Manager client servicing client servicing jobs Find all jobs matching client servicing client management client management jobs Find all jobs matching client management Client Relation client relation jobs Find all jobs matching Client Relation clients retention client retention jobs Find all jobs matching clients retention Recruitment recruitment jobs Find all j

In [13]:
clean_text = []
for text in pp.progressbar(job_description_en): 
    clean_text.append(clean_str(text))

100% (403472 of 403472) |################| Elapsed Time: 0:02:51 Time:  0:02:51


In [ ]:
## save clean data
with open('clean_text_single_gram', 'wb') as ct:
    pickle.dump(clean_text, ct)

In [16]:
print(clean_text[-10:])

['Principle Objective To achieve and or exceed sales plan by creating and maintaining successful Tom Ford Beauty By Kilian and Editions de Parfums Frederic Malle Specialist teams. Create strategic partnerships with retail partners to grow the brands. Responsibilities include selection development and retention of Sales Education Coordinators and counter staff administration of point of sale initiatives and management of the account at a store level. Accountabilities 1 Lead and Execute Tom Ford Beauty By Kilian and Editions de Parfums Frederic Malle Initiatives Work with Brand Manager to plan and achieve retail sales goals by door. Communicate and cascade goals objectives and priorities to sales education coordinators counter business managers and specialists on a weekly basis. Create store- specific action plans to achieve counter goals and objectives. Collaborate with sales and education coordinators to ensure execution of those plans. Plan and execute new product launches and special

In [22]:
## train word2vec without specify skills
import gensim

tokenized_text = []
for text in pp.progressbar(clean_text):
    tokenized_text.append(gensim.utils.simple_preprocess(text))
    
print(tokenized_text[:10])

100% (170060 of 170060) |################| Elapsed Time: 0:02:16 Time:  0:02:16


[['wealth', 'management', 'credit', 'risk', 'analyst', 'wealth', 'management', 'wm', 'provides', 'advice', 'strategies', 'and', 'solutions', 'for', 'all', 'aspects', 'of', 'the', 'financial', 'asset', 'management', 'and', 'wealth', 'transfer', 'needs', 'of', 'high', 'net', 'worth', 'and', 'ultra', 'high', 'net', 'worth', 'clients', 'wm', 'is', 'dedicated', 'to', 'delivering', 'an', 'outstanding', 'client', 'experience', 'by', 'providing', 'unbiased', 'advice', 'and', 'individual', 'solutions', 'credit', 'risk', 'assesses', 'permissions', 'and', 'manages', 'credit', 'and', 'counterparty', 'risks', 'on', 'an', 'industry', 'client', 'geographic', 'and', 'transaction', 'basis', 'credit', 'risk', 'is', 'the', 'risk', 'of', 'loss', 'arising', 'from', 'the', 'default', 'of', 'client', 'or', 'counterparty', 'the', 'credit', 'risk', 'function', 'identifies', 'measures', 'limits', 'manages', 'and', 'monitors', 'credit', 'risk', 'across', 'our', 'businesses', 'credit', 'exposure', 'arises', 'thro

In [25]:
model = gensim.models.Word2Vec(tokenized_text, size=500, window=10, min_count=5)
model.save("word2vec.model")

In [29]:
import logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)

model = gensim.models.Word2Vec.load("word2vec.model")
model.train(tokenized_text, total_examples=len(tokenized_text), epochs=10)

2018-09-12 11:52:50,569 : INFO : loading Word2Vec object from word2vec.model
2018-09-12 11:52:50,945 : INFO : loading wv recursively from word2vec.model.wv.* with mmap=None
2018-09-12 11:52:50,947 : INFO : loading vectors from word2vec.model.wv.vectors.npy with mmap=None
2018-09-12 11:52:51,243 : INFO : setting ignored attribute vectors_norm to None
2018-09-12 11:52:51,305 : INFO : loading vocabulary recursively from word2vec.model.vocabulary.* with mmap=None
2018-09-12 11:52:51,307 : INFO : loading trainables recursively from word2vec.model.trainables.* with mmap=None
2018-09-12 11:52:51,310 : INFO : loading syn1neg from word2vec.model.trainables.syn1neg.npy with mmap=None
2018-09-12 11:52:51,737 : INFO : setting ignored attribute cum_table to None
2018-09-12 11:52:51,742 : INFO : loaded word2vec.model
2018-09-12 11:52:51,871 : WARNING : Effective 'alpha' higher than previous training cycles
2018-09-12 11:52:51,873 : INFO : training model with 3 workers on 60417 vocabulary and 500 fea

2018-09-12 11:53:57,632 : INFO : EPOCH 1 - PROGRESS: at 56.35% examples, 542140 words/s, in_qsize 6, out_qsize 0
2018-09-12 11:53:58,657 : INFO : EPOCH 1 - PROGRESS: at 57.10% examples, 540841 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:53:59,686 : INFO : EPOCH 1 - PROGRESS: at 57.88% examples, 539708 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:54:00,710 : INFO : EPOCH 1 - PROGRESS: at 58.50% examples, 538529 words/s, in_qsize 4, out_qsize 1
2018-09-12 11:54:01,722 : INFO : EPOCH 1 - PROGRESS: at 59.07% examples, 537514 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:54:02,725 : INFO : EPOCH 1 - PROGRESS: at 59.73% examples, 536594 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:54:03,736 : INFO : EPOCH 1 - PROGRESS: at 60.46% examples, 536183 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:54:04,753 : INFO : EPOCH 1 - PROGRESS: at 61.22% examples, 536277 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:54:05,768 : INFO : EPOCH 1 - PROGRESS: at 61.89% examples, 535909 words/s, in_qsiz

2018-09-12 11:55:08,307 : INFO : EPOCH 2 - PROGRESS: at 8.52% examples, 511783 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:55:09,318 : INFO : EPOCH 2 - PROGRESS: at 9.45% examples, 512673 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:55:10,321 : INFO : EPOCH 2 - PROGRESS: at 10.28% examples, 511842 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:55:11,331 : INFO : EPOCH 2 - PROGRESS: at 11.13% examples, 510745 words/s, in_qsize 6, out_qsize 0
2018-09-12 11:55:12,358 : INFO : EPOCH 2 - PROGRESS: at 12.01% examples, 506572 words/s, in_qsize 4, out_qsize 1
2018-09-12 11:55:13,374 : INFO : EPOCH 2 - PROGRESS: at 12.75% examples, 503319 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:55:14,386 : INFO : EPOCH 2 - PROGRESS: at 13.58% examples, 504440 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:55:15,395 : INFO : EPOCH 2 - PROGRESS: at 14.48% examples, 506774 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:55:16,397 : INFO : EPOCH 2 - PROGRESS: at 15.27% examples, 502968 words/s, in_qsize 

2018-09-12 11:56:22,099 : INFO : EPOCH 2 - PROGRESS: at 65.48% examples, 499878 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:56:23,112 : INFO : EPOCH 2 - PROGRESS: at 66.30% examples, 499582 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:56:24,114 : INFO : EPOCH 2 - PROGRESS: at 67.07% examples, 499159 words/s, in_qsize 6, out_qsize 0
2018-09-12 11:56:25,125 : INFO : EPOCH 2 - PROGRESS: at 67.91% examples, 498878 words/s, in_qsize 6, out_qsize 0
2018-09-12 11:56:26,130 : INFO : EPOCH 2 - PROGRESS: at 68.53% examples, 497572 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:56:27,148 : INFO : EPOCH 2 - PROGRESS: at 69.25% examples, 496842 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:56:28,174 : INFO : EPOCH 2 - PROGRESS: at 69.96% examples, 496226 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:56:29,178 : INFO : EPOCH 2 - PROGRESS: at 70.61% examples, 495626 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:56:30,182 : INFO : EPOCH 2 - PROGRESS: at 71.22% examples, 495136 words/s, in_qsiz

2018-09-12 11:57:32,141 : INFO : EPOCH 3 - PROGRESS: at 21.37% examples, 521461 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:33,144 : INFO : EPOCH 3 - PROGRESS: at 22.32% examples, 522410 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:34,164 : INFO : EPOCH 3 - PROGRESS: at 23.29% examples, 523775 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:35,174 : INFO : EPOCH 3 - PROGRESS: at 24.12% examples, 523277 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:36,199 : INFO : EPOCH 3 - PROGRESS: at 24.96% examples, 521253 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:37,207 : INFO : EPOCH 3 - PROGRESS: at 25.87% examples, 520976 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:38,219 : INFO : EPOCH 3 - PROGRESS: at 26.64% examples, 520238 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:39,221 : INFO : EPOCH 3 - PROGRESS: at 27.51% examples, 520384 words/s, in_qsize 5, out_qsize 0
2018-09-12 11:57:40,237 : INFO : EPOCH 3 - PROGRESS: at 28.41% examples, 521660 words/s, in_qsiz

...

2018-09-12 12:10:45,318 : INFO : EPOCH 9 - PROGRESS: at 20.57% examples, 503626 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:46,331 : INFO : EPOCH 9 - PROGRESS: at 21.44% examples, 503721 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:47,332 : INFO : EPOCH 9 - PROGRESS: at 22.36% examples, 504711 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:48,336 : INFO : EPOCH 9 - PROGRESS: at 23.23% examples, 504972 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:49,336 : INFO : EPOCH 9 - PROGRESS: at 24.05% examples, 505291 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:50,368 : INFO : EPOCH 9 - PROGRESS: at 24.99% examples, 505421 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:51,373 : INFO : EPOCH 9 - PROGRESS: at 25.87% examples, 505461 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:52,381 : INFO : EPOCH 9 - PROGRESS: at 26.64% examples, 505045 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:10:53,410 : INFO : EPOCH 9 - PROGRESS: at 27.48% examples, 504282 words/s, in_qsiz

2018-09-12 12:11:59,238 : INFO : EPOCH 9 - PROGRESS: at 78.19% examples, 505000 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:00,242 : INFO : EPOCH 9 - PROGRESS: at 78.97% examples, 505304 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:01,249 : INFO : EPOCH 9 - PROGRESS: at 79.67% examples, 505468 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:02,257 : INFO : EPOCH 9 - PROGRESS: at 80.43% examples, 505866 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:03,271 : INFO : EPOCH 9 - PROGRESS: at 81.18% examples, 506321 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:04,280 : INFO : EPOCH 9 - PROGRESS: at 81.94% examples, 506657 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:05,280 : INFO : EPOCH 9 - PROGRESS: at 82.60% examples, 506020 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:06,286 : INFO : EPOCH 9 - PROGRESS: at 83.25% examples, 505498 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:12:07,290 : INFO : EPOCH 9 - PROGRESS: at 84.05% examples, 505709 words/s, in_qsiz

2018-09-12 12:13:09,759 : INFO : EPOCH 10 - PROGRESS: at 33.32% examples, 507577 words/s, in_qsize 6, out_qsize 0
2018-09-12 12:13:10,764 : INFO : EPOCH 10 - PROGRESS: at 34.02% examples, 507753 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:11,775 : INFO : EPOCH 10 - PROGRESS: at 34.77% examples, 507425 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:12,796 : INFO : EPOCH 10 - PROGRESS: at 35.59% examples, 507985 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:13,799 : INFO : EPOCH 10 - PROGRESS: at 36.37% examples, 508311 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:14,815 : INFO : EPOCH 10 - PROGRESS: at 37.14% examples, 507589 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:15,841 : INFO : EPOCH 10 - PROGRESS: at 37.92% examples, 507480 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:16,854 : INFO : EPOCH 10 - PROGRESS: at 38.73% examples, 507970 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:13:17,858 : INFO : EPOCH 10 - PROGRESS: at 39.54% examples, 508476 words/s

2018-09-12 12:14:23,014 : INFO : EPOCH 10 - PROGRESS: at 81.41% examples, 456509 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:14:24,030 : INFO : EPOCH 10 - PROGRESS: at 81.79% examples, 454951 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:14:25,048 : INFO : EPOCH 10 - PROGRESS: at 82.40% examples, 454672 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:14:26,057 : INFO : EPOCH 10 - PROGRESS: at 83.02% examples, 454439 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:14:27,062 : INFO : EPOCH 10 - PROGRESS: at 83.65% examples, 454261 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:14:28,082 : INFO : EPOCH 10 - PROGRESS: at 84.22% examples, 453607 words/s, in_qsize 5, out_qsize 0
2018-09-12 12:14:29,087 : INFO : EPOCH 10 - PROGRESS: at 84.92% examples, 453668 words/s, in_qsize 6, out_qsize 0
2018-09-12 12:14:30,101 : INFO : EPOCH 10 - PROGRESS: at 85.62% examples, 453193 words/s, in_qsize 6, out_qsize 0
2018-09-12 12:14:31,117 : INFO : EPOCH 10 - PROGRESS: at 86.41% examples, 453112 words/s

(643229407, 779594330)

In [97]:
test_list = ["python", "java", "engineer", "excel", "windows", "supply", "finance", "law", "volkswagen", "microsoft", "ms", "id"]

for word in test_list:
    print(word, ":\n", model.wv.most_similar(word, topn=10))

python :
 [('java', 0.5775786638259888), ('programming', 0.5024352073669434), ('scripting', 0.49300575256347656), ('scala', 0.48204708099365234), ('sql', 0.45646244287490845), ('vba', 0.45345473289489746), ('matlab', 0.4523012042045593), ('linux', 0.44909530878067017), ('erlang', 0.4474000930786133), ('programing', 0.44161373376846313)]
java :
 [('python', 0.5775786638259888), ('scala', 0.492953360080719), ('sql', 0.48523861169815063), ('fspring', 0.4649026095867157), ('web', 0.45784538984298706), ('multithreading', 0.45341354608535767), ('ror', 0.45115312933921814), ('dojo', 0.450187623500824), ('angular', 0.44846874475479126), ('nodejs', 0.4470083713531494)]
engineer :
 [('developer', 0.6307722330093384), ('technician', 0.48629868030548096), ('architect', 0.48340022563934326), ('engineering', 0.47516053915023804), ('analyst', 0.46210309863090515), ('specialist', 0.444033682346344), ('engineers', 0.38512903451919556), ('administrator', 0.38083726167678833), ('manager', 0.3735758066177

In [85]:
print(len(model.wv.vocab))

60417


In [92]:
## get skills with single word

skill_names = pd.read_csv("../SkillMatch/skill_name.csv").name
skill_names = skill_names.unique()

# remove the contents inside () and spaces
keys = []
for key in skill_names:
    key = re.sub(r'\([^)]*\)', '', key)  ## remove the contents inside ()
    key = re.sub(r'\(.*?', '', key)
    key = re.sub(r'\s+$', '', key)
    keys.append(key)

p = re.compile(r'[\s]+')
p.search(keys[0])
single_gram = [key.lower() for key in keys if not p.search(key)]

#print(single_gram)

for n, key in enumerate(single_gram):
    if key in model.wv.vocab:
        print(n, ".", key, ":\n", model.wv.most_similar(key, topn=10))

0 . aeronautics :
 [('compenstaion', 0.3155566453933716), ('oopd', 0.3140553832054138), ('aerospace', 0.29555875062942505), ('falsifying', 0.2882545292377472), ('prefd', 0.28357526659965515), ('wstern', 0.2721080780029297), ('electronical', 0.26889747381210327), ('walkerhamill', 0.2602077126502991), ('proffered', 0.25234779715538025), ('exprience', 0.2514776885509491)]
1 . aircraft :
 [('airframe', 0.44175463914871216), ('flight', 0.3870462477207184), ('overhaul', 0.3856665790081024), ('ships', 0.36923855543136597), ('satellites', 0.3688507378101349), ('airworthiness', 0.36622118949890137), ('uav', 0.36233291029930115), ('compressors', 0.3573465943336487), ('refrigeration', 0.3547694683074951), ('belts', 0.3534882068634033)]
2 . aviation :
 [('lccs', 0.3723999559879303), ('airline', 0.36982518434524536), ('aerospace', 0.35981428623199463), ('marine', 0.3429199457168579), ('ports', 0.3315504491329193), ('aeronautical', 0.3294937312602997), ('aircraft', 0.32152748107910156), ('airports',

57 . honda :
 [('volvo', 0.5496788024902344), ('hyundai', 0.521776556968689), ('vw', 0.47450122237205505), ('bugatti', 0.4211973249912262), ('nissan', 0.41895216703414917), ('jcb', 0.4126511216163635), ('suzuki', 0.40954768657684326), ('maruti', 0.4025025963783264), ('volkswagen', 0.39537572860717773), ('audi', 0.39409542083740234)]
58 . hyundai :
 [('kia', 0.6074517965316772), ('honda', 0.521776556968689), ('showroom', 0.386985719203949), ('volvo', 0.3764187693595886), ('bolands', 0.3735511004924774), ('nissan', 0.35592007637023926), ('vw', 0.3541685938835144), ('glovis', 0.35096919536590576), ('maruti', 0.34807318449020386), ('leadeing', 0.3460739254951477)]
59 . man :
 [('torrent', 0.3536461889743805), ('ahl', 0.3263595998287201), ('sqids', 0.3189420700073242), ('yog', 0.31096428632736206), ('qna', 0.2988274097442627), ('pme', 0.2973634600639343), ('consultingkrew', 0.29704415798187256), ('businesswoman', 0.2964341640472412), ('isle', 0.2949351668357849), ('deprived', 0.276814162731

101 . railways :
 [('switchgears', 0.5768593549728394), ('cement', 0.4459576904773712), ('durables', 0.4212280511856079), ('ites', 0.42110657691955566), ('biotech', 0.4201053977012634), ('hospitals', 0.4147491753101349), ('foods', 0.4028860330581665), ('quarrying', 0.3970138430595398), ('anciliary', 0.3953944146633148), ('garments', 0.3941216468811035)]
102 . service :
 [('satisfaction', 0.4305467903614044), ('services', 0.4258422553539276), ('care', 0.3496975898742676), ('swiftnet', 0.3107963502407074), ('mont', 0.3052257299423218), ('kiara', 0.29868245124816895), ('centricity', 0.2967149019241333), ('consignments', 0.28937816619873047), ('statusing', 0.2847689390182495), ('zgvlcgfrlmpoys', 0.2833629846572876)]
103 . technology :
 [('technologies', 0.4285985231399536), ('infrastructure', 0.3454377055168152), ('cloud', 0.34115153551101685), ('security', 0.34068578481674194), ('enterprise', 0.33151015639305115), ('deltron', 0.3116339445114136), ('systems', 0.3076784312725067), ('digital

156 . clarification :
 [('clarify', 0.2841337025165558), ('clarifications', 0.27905696630477905), ('definition', 0.25283747911453247), ('missing', 0.2491457611322403), ('inform', 0.24457678198814392), ('explanation', 0.23412269353866577), ('review', 0.22891424596309662), ('interpretation', 0.22629690170288086), ('doubt', 0.22561822831630707), ('questions', 0.2241244912147522)]
158 . innovative :
 [('breakthrough', 0.379488468170166), ('innovation', 0.378127783536911), ('creative', 0.3764621615409851), ('our', 0.32733577489852905), ('innovate', 0.30476561188697815), ('unconventional', 0.2956576347351074), ('sustainable', 0.2950995862483978), ('softinent', 0.2923673987388611), ('differentiated', 0.2892257273197174), ('innovations', 0.28916430473327637)]
159 . interpretation :
 [('interpreting', 0.3421461582183838), ('interpret', 0.32221361994743347), ('interpretations', 0.32029542326927185), ('analysis', 0.3025391697883606), ('evaluation', 0.27655354142189026), ('inaccurate', 0.264940559

191 . supervising :
 [('directing', 0.4231695532798767), ('managing', 0.3987138271331787), ('supervises', 0.3973972797393799), ('overseeing', 0.3968190550804138), ('assigning', 0.38381972908973694), ('supervise', 0.37448564171791077), ('coordinating', 0.35340166091918945), ('assisting', 0.3218441903591156), ('instructing', 0.31831756234169006), ('delegating', 0.31199800968170166)]
192 . objective :
 [('goal', 0.4558486342430115), ('purpose', 0.3599151372909546), ('aim', 0.3445310592651367), ('mission', 0.3367312550544739), ('objectives', 0.2915349304676056), ('intention', 0.24958649277687073), ('职位描述', 0.2433479130268097), ('rbpm', 0.21925634145736694), ('intent', 0.2160957157611847), ('remetrica', 0.21517795324325562)]
193 . patience :
 [('empathy', 0.5565260052680969), ('courtesy', 0.392360657453537), ('honesty', 0.36831966042518616), ('tact', 0.3651352524757385), ('humility', 0.3614833354949951), ('professionalism', 0.35592561960220337), ('perseverance', 0.35430729389190674), ('sinc

...

 [('stooping', 0.6368041634559631), ('kneeling', 0.5915015339851379), ('twisting', 0.5720603466033936), ('lifting', 0.5311342477798462), ('crouching', 0.5168494582176208), ('squatting', 0.45313766598701477), ('crawling', 0.4342278242111206), ('climbing', 0.4308854043483734), ('fingering', 0.41957417130470276), ('walking', 0.40745487809181213)]
1282 . casting :
 [('aluminium', 0.47808563709259033), ('machining', 0.4491662383079529), ('cipet', 0.3709501028060913), ('impregnation', 0.3616301119327545), ('machined', 0.35741013288497925), ('maldaner', 0.34148019552230835), ('stamping', 0.33119383454322815), ('aluminum', 0.32494181394577026), ('moulding', 0.3245317339897156), ('die', 0.32328397035598755)]
1284 . polishing :
 [('stripping', 0.4738568365573883), ('sinking', 0.46567970514297485), ('painting', 0.45260089635849), ('washing', 0.45147573947906494), ('waxing', 0.43898630142211914), ('rugs', 0.43153446912765503), ('trimming', 0.4235886335372925), ('shampooing', 0.42051562666893005), 

1324 . aida :
 [('aifm', 0.48830896615982056), ('mnpi', 0.31613466143608093), ('timessquare', 0.2732437252998352), ('schroder', 0.2705504596233368), ('eesti', 0.26822608709335327), ('sfs', 0.2620547413825989), ('securitised', 0.25801652669906616), ('leftpart', 0.25531214475631714), ('tradable', 0.2544821500778198), ('menopt', 0.25249946117401123)]
1325 . promotion :
 [('promotions', 0.4014246165752411), ('promotional', 0.30516305565834045), ('layoffs', 0.28261101245880127), ('natchez', 0.2643430531024933), ('branding', 0.2573978304862976), ('infotronics', 0.25605934858322144), ('layoff', 0.24890974164009094), ('incentive', 0.2410794198513031), ('btl', 0.23742786049842834), ('marketing', 0.2374027967453003)]
1326 . sponsorship :
 [('visa', 0.44370508193969727), ('visas', 0.3936161696910858), ('relocation', 0.35813838243484497), ('sponsor', 0.33637070655822754), ('authorized', 0.2903967499732971), ('tyes', 0.2808583378791809), ('restriction', 0.26875683665275574), ('micromanagement', 0.2

1384 . paramedic :
 [('emt', 0.6014850735664368), ('bcls', 0.49981689453125), ('pals', 0.46021902561187744), ('acls', 0.45614659786224365), ('phlebotomist', 0.44991636276245117), ('rvt', 0.44577446579933167), ('rn', 0.4446284770965576), ('paramedics', 0.4438907504081726), ('cot', 0.4345861077308655), ('ekg', 0.43295782804489136)]
1385 . hematology :
 [('immunology', 0.5656769871711731), ('microbiology', 0.555005669593811), ('coagulation', 0.5309491157531738), ('serology', 0.49902862310409546), ('bacteriology', 0.4871670603752136), ('hematologist', 0.48279550671577454), ('pharmacology', 0.4545583128929138), ('mycology', 0.4485095143318176), ('hematological', 0.43464264273643494), ('molecular', 0.43451806902885437)]
1386 . surgeon :
 [('neuro', 0.6980687379837036), ('neurologist', 0.6341366171836853), ('cardiologist', 0.6321398019790649), ('neurosurgery', 0.6247150301933289), ('ortho', 0.6215180158615112), ('neurology', 0.6123178601264954), ('anaesthetist', 0.5990053415298462), ('intensi

1433 . photonics :
 [('photonic', 0.41232526302337646), ('modulators', 0.390424907207489), ('optics', 0.386584997177124), ('metallurgy', 0.3794790506362915), ('optoelectronic', 0.37211742997169495), ('microscopy', 0.3599189817905426), ('dielectric', 0.3463166356086731), ('detectors', 0.34598517417907715), ('semiconductor', 0.3406631052494049), ('spectrometer', 0.3399394154548645)]
1434 . psychometrics :
 [('inaugural', 0.3363485634326935), ('defender', 0.3320438265800476), ('xnxc', 0.32876360416412354), ('shl', 0.3253658413887024), ('vidyagram', 0.3083075284957886), ('wusf', 0.30342569947242737), ('fuy', 0.2950402498245239), ('servants', 0.28448212146759033), ('nlje', 0.2766815721988678), ('hearty', 0.269339382648468)]
1435 . biostatistics :
 [('epidemiology', 0.5313064455986023), ('immunology', 0.45300203561782837), ('bioinformatics', 0.4440264105796814), ('pharmacology', 0.43389755487442017), ('microbiology', 0.4118228554725647), ('biochemistry', 0.4051993489265442), ('statistician',

1503 . anatomy :
 [('physiology', 0.7658408880233765), ('beings', 0.4616856575012207), ('rays', 0.426972895860672), ('pathology', 0.4257751703262329), ('resouce', 0.42459404468536377), ('ultrasound', 0.40503358840942383), ('ophthalmology', 0.39615654945373535), ('radiographic', 0.39594584703445435), ('histology', 0.3884315490722656), ('tissues', 0.38561415672302246)]
1505 . infections :
 [('diseases', 0.569729208946228), ('communicable', 0.5065743327140808), ('illnesses', 0.5015957355499268), ('disease', 0.4882206320762634), ('infectious', 0.4690267741680145), ('depression', 0.4689388573169708), ('newborns', 0.4661564826965332), ('hypertension', 0.45241689682006836), ('colds', 0.45182234048843384), ('asthma', 0.44920551776885986)]
1506 . pediatrics :
 [('nicu', 0.6317653059959412), ('orthopedics', 0.6109651327133179), ('endocrinology', 0.596618115901947), ('gynecology', 0.5948292016983032), ('neonatology', 0.593416154384613), ('nephrology', 0.579390287399292), ('pediatric', 0.578712701

In [116]:
## keys include special charaters, (for the phrase2vec model, ignore them first)
number_letter = re.compile(r'^[a-zA-Z0-9\s]*$')

key_special = [key.lower() for key in keys if not number_letter.search(key)]
print(len(key_special))

892


In [238]:
## Phrase2Vec

example = job_description_en[2310]

from gensim.models.phrases import Phrases, Phraser

clean_sample = [[u'the', u'mayor', u'of', u'new', u'york', u'was', u'there'], 
 [u'machine', u'learning', u'can', u'be', u'new', u'york' , u'sometimes']]
#gensim.utils.simple_preprocess(clean_str(example))

## stop list
stop_words = set(stopwords.words('english'))
words_need = ['s','and', 'of']
for word in words_need:
    stop_words.remove(word)


example = space.sub(" ", example).strip()

punct = re.compile("[.,;!?:*()=/\\\[\]•#_§\$€]+")  # heavily depends on the text
coarse_candidates = punct.split(example.lower())
## clean whitespace and empty string
candidates = [sent.strip() for sent in coarse_candidates if sent.strip()]

for sent in candidates:
    sent = re.split('\s+', sent)
    a = ["|" if w in stop_words else w for w in sent]
    
    print(a)
    

#print(candidates)

#phrases = Phrases(clean_sample, min_count=1, threshold=1)
#bigram = Phraser(phrases)
#bigram[clean_sample[1]]

['working', 'student', '-', 'virtual', 'integration', 'environment']
['|']
['f']
['description']
['|', '|', 'area', 'of', 'virtual', 'integration', 'environment', '|', '|', 'looking', '|', '|', 'working', 'student']
['|']
['f']
['|', 'lindau', 'beginning', '|', 'soon', '|', 'possible', '|', '4', '|', '6', 'months', 'and', 'max']
['20', 'hours', 'per', 'week']
['|', 'working', 'student', '|', '|', '|', '|', 'possibility', 'of', 'working', '|', '|', 'challenging', 'environment', '|', 'state-of-the-art', 'adas', 'technologies', 'and', 'enjoy', 'setting', '|', 'automated', 'testing', 'environments', '|', '|', 'critical', '|', '|', 'success', 'of', '|', 'integration', 'activities']
['|', 'tasks', 'include']
['implementation', 'of', 'automation', '|', 'testing', 'scripts']
['standardization', 'among', 'different', 'technologies']
['unit', 'testing', '|', '|', 'tooling']
['roll-out', 'of', 'scripts', 'and', 'presentation']
['technical', 'support']
['assessment', 'of', 'results']
['qualificati

In [184]:
## match and connect words

#text = "Surround View / Omniview Mobile In-Vehicle Applications Vehicle-Network Radar - ARSx, Technology, Media & Communications \
#        Aeronautics, Aircraft, Aviation, Aircraft Wing, jet Engine, DO178B, avionics A330"

def match(text):
    for key in keys:
        p = re.escape(key)
        c = re.compile(r"\b"+ p + r"\b", re.I)
        key_re = key.replace(" ", "_")
        text = c.sub(key_re, text)
    return text

#    matched_text = match(clean_text)
#    whole_text.append(matched_text)

100% (170060 of 170060) |################| Elapsed Time: 0:00:53 Time:  0:00:53


In [231]:
whole_text = " | ".join(clean_text[:500])
p = []
for key in keys:
    p.append(re.escape(key))

p = "|".join(p)
c = re.compile(r"\("+ p + r"\)", re.I)
match = c.sub(lambda match: match.group(0).replace(" ","_"), whole_text)


print(match)

"""for key in pp.progressbar(keys):
    p = re.escape(key)
    c = re.compile(r"\b"+ p + r"\b", re.I)
    key_re = key.replace(" ", "_")
    whole_text = c.sub(key_re, whole_text)  

print(whole_text)"""

Wealth Management - Credit Risk Analyst Wealth Management WM provides advice strategies and solutions for all aspects of the financial asset management and wealth transfer needs of high net worth and ultra-high net worth clients. WM is dedicated to delivering an outstanding client experience by providing unbiased advice and individual solutions. Credit Risk assesses permissions and manages credit and counterparty risks on an industry client geographic and transaction basis. Credit risk is the risk of loss arising from the default of a client or counterparty. The Credit Risk function identifies measures limits manages and monitors credit risk across our businesses. Credit exposure arises through underwriting lending and trading activities with and for clients and counterparties as well as from a range of operating services such as cash_management and clearing activities. Responsibilities Evaluate WM consumer and business purpose credit requests utilizing applicable Credit Risk Policies 

'for key in pp.progressbar(keys):\n    p = re.escape(key)\n    c = re.compile(r"\x08"+ p + r"\x08", re.I)\n    key_re = key.replace(" ", "_")\n    whole_text = c.sub(key_re, whole_text)  \n\nprint(whole_text)'

In [224]:
## for test

dt = "a b, ef,c d e ,kk, c d e   , a b,"

#c = re.compile(r"\ba\sb|c\sd\se\b", re.I)
#c.sub(lambda m: m.group(0).replace(" ","_"), dt)

mass = "ABCD EFGH IJKL"
part = re.sub('(a\sb|c\sd\se).', lambda match: match.group(1).replace(" ","_"), dt)
print(part)

a_b, ef,c_d_e_,kk, c_d_e_  , a_b,


In [187]:
re.split(r"\|", whole_text)

['Wealth Management - Credit_risk Analyst Wealth Management WM provides advice strategies and solutions for all aspects of the financial asset management and wealth transfer needs of high net worth and ultra-high net worth clients. WM is dedicated to delivering an outstanding client experience by providing unbiased advice and individual solutions. Credit_risk assesses permissions and manages credit and counterparty risks on an Industry client geographic and transaction basis. Credit_risk is the risk of loss arising from the default of a client or counterparty. The Credit_risk function identifies measures limits manages and monitors Credit_risk across our businesses. Credit exposure arises through underwriting lending and trading activities with and for clients and counterparties as well as from a range of operating services such as Cash_Management and clearing activities. Responsibilities Evaluate WM consumer and Business purpose credit requests utilizing applicable Credit_risk Policie

In [109]:
text = "Surround View / Omniview Mobile In-Vehicle Applications Vehicle-Network Radar - ARSx , \
        Aeronautics, Aircraft, Aviation, Aircraft Wing, jet Engine, DO178B, avionics A330"
a = []
for key in key_sp:
    p = re.escape(key)
    c = re.compile(r"\b"+ p + r"\b", re.I)
    key_re = key.replace(" ", "_")
    text = c.sub(key_re, text)

    #a.append(key)

print(text)

#c = re.compile("[,;\'\&\(\)]+")
#    key = re.escape(key)
#    re.sub(c, r"\\\1", key) 
#    str.replace(/[<>*()?]/g, "\\$&");
#    key.replace(/[()]/g, "\\$&")
    #if c.findall(key):
        #key = re.sub(c, '\', 
#    key_special.append(key)
    
#key_special

Surround  View / Omniview Mobile_In-Vehicle_Applications Vehicle-Network Radar_-_ARSx Technology,_Media_&_Communications,         Aeronautics, Aircraft, Aviation, Aircraft Wing, jet Engine, DO178B, avionics A330


In [53]:
#for n, job_text in enumerate(job_description_df.job_description[:1000]):
#    string = "Microsoft Office"
#    skill_re = " "+string.replace(" ", "_")+" "
#    match = re.findall(string, job_text, flags=re.I)
#    if match:
#        print(n)
#        sub_text = re.sub(string, skill_re, job_text, flags=re.I)

#print(sub_text)


#c=re.compile(r"\bC\b",re.I)
#c.findall(example)

example = job_description_en[141]
#print(example)

for i, key in enumerate(skills):
    c = re.compile(r"\b"+key+r"\b",re.I)
    match = c.findall(example)
    if match:
        key_re = key.replace(" ", "_")
        print(key_re)
        print("match!", key, key_re)
        example = c.sub(key_re, example)
    #except:
    #    print(key)

#print(example)
#    if example.find(key) != -1:
#        print(i,key, "match!")
#        print(key.replace(" ", "_"))
#        example.replace(key, key.replace(" ", "_"))
    
#print(example)


#print(skills)
#f = open("../SkillMatch/skill_name.csv")
#keys = f.read()
#print(keys)

#pattern = re.compile(r'\b(' + keys + r')\b\s*', re.IGNORECASE)

#for text in job_description_en[:1000]:
#    match = re.findall(pattern, clean_str(example))
#    if match:
#        print(match)

error: multiple repeat at position 4

In [24]:
# remove stopwords

stop_words = set(stopwords.words('english'))
stop_words.remove('s')

def rm_stopwords(s):
    pattern = 
    text = pattern.sub('', s)
    return text

print(rm_stopwords(example))
#filtered_text = [w for w in word_tokenize(example) if not w in stop_words]
#filtered_text


from textacy import preprocess
#    s = preprocess.preprocess_text(text, fix_unicode=True, lowercase=True, transliterate=True, no_urls=True, no_emails=True, no_phone_numbers=True, no_numbers=True, no_currency_symbols=True)  ## remove url

SyntaxError: invalid syntax (<ipython-input-24-964b3d642a11>, line 7)

In [50]:
for text in tqdm(job_description_en[:10000]):
    clean_str(text)
    

100%|██████████| 10000/10000 [00:03<00:00, 2817.67it/s]


In [30]:
def compute_ngrams(tokens, max_len = None, min_len = 1):
    """tokens  :   iterable of string
                    a single sentence of tokens. Assumes start and stop tokens omitted
    max_len :   int
                    maximum ngram length
    min_len :   int
                    minimum ngram length

    """
    if max_len == None:
        max_len = len(tokens)

    if min_len > max_len:
        raise Exception("min_len cannot be more than max_len")

    ngrams = set()
    # unigrams
    for ngram_size in range(min_len, max_len + 1):
        for start in range(0, len(tokens) - ngram_size + 1):
            end = start + ngram_size -1
            words = []
            for i in range(start, end + 1):
                words.append(tokens[i])
            ngrams.add(tuple(words)) # make a tuple so hashable
    return ngrams

# is a valid token
__bad_chars__ = "<>{}[]~@"
__punct__ = set(".?!,;:")
def is_valid_term(term):
    # remove single char entries and only numeric
    if len(term) == 0:
        return False
    if len(term) == 1:
        #else misses c and r
        if term.isalpha():
            return True
        return False
    # no html or js terms
    for c in __bad_chars__:
        if c in term:
            return False
    if term[-1] in __punct__:
        return False
    if "function(" in term:
        return False
    if "!" in term or "?" in term:
        return False
    digit_chars = 0.0
    for c in term:
        if c.isdigit() or not c.isalnum():
            digit_chars += 1.0
    # 60% digits?
    if (digit_chars / len(term)) >= 0.75:
        return False
    return True



In [ ]:
re_collapse_spaces = re.compile("\s+")

# collapse space
def collapse_spaces(s):
    return re_collapse_spaces.sub(" ", s).strip()

In [ ]:
## Define variables from database

job_table = "jobs"
job_id_column = "job_id"

job_skill_table = "job_skill_mapping"
skill_id_column = "skill_id"

skill_tree_table = "dem_skill"
skill_tree_id_column = "skill_id"
skill_tree_parent_column = "skill_parent_id"
skill_tree_level_column = "skill_hierarchy_id"

skill_name_table = "language_dem_skill"
skill_name_id_column = "skill_id"
skill_name_name_column = "skill_name"
skill_name_language_id = "language_id"


# create id skill dictionary (level 5)
command = 'select skill_id, skill_name from language_dem_skill \
            where skill_id in (select skill_id from dem_skill where skill_hierarchy_id = 5)'


skills_level5 = pd.read_sql_query(text(command), con = engine)
skills_level5 = skills_level5.drop_duplicates(subset="skill_id", keep='first', inplace=False)
skills_level5

In [ ]:
#values = re.findall(pattern=measurement, string=text)
#sub_text = re.sub(pattern=measurement, string=text, repl='MEASUREMENT')

for n, job_text in enumerate(job_description_df.job_description[:1000]):
    string = "Microsoft Office"
    skill_re = " "+string.replace(" ", "_")+" "
    match = re.findall(string, job_text, flags=re.I)
    if match:
        print(n)
        sub_text = re.sub(string, skill_re, job_text, flags=re.I)
        print(sub_text)

In [ ]:
## find skills containing regular and special characters

key_sp = []
key_reg = []
for key in keys:
    if re.match("^[A-Za-z0-9_\s]*$", key):
        key_reg.append(key)
    else:
        key_sp.append(key)
print(key_reg[:10])   
print(key_sp[:30])